In [1]:
import pandas as pd
import folium
from folium.plugins import HeatMapWithTime
from folium.plugins import HeatMap
from folium.plugins import MarkerCluster

In [2]:
df=pd.read_csv('../data/berlin_accidents.csv')

In [3]:
df.head()

Unnamed: 0  OBJECTID  UMONAT  USTUNDE  UWOCHENTAG  UKATEGORIE  UART  UTYP1  \
0           0    112747       1       15           4           3     6      7   
1           1    112892       1       11           5           3     5      2   
2           2    112902       1        8           2           3     5      2   
3           3    112921       1       19           4           3     5      7   
4           4    112947       1       18           4           2     5      3   

   ULICHTVERH  STRZUSTAND  ...  IstKrad  IstGkfz  IstFuss  IstSonstige  \
0           1           1  ...        0        0        1            0   
1           0           1  ...        0        0        0            0   
2           0           0  ...        0        0        0            0   
3           2           1  ...        0        0        0            0   
4           2           1  ...        0        0        0            0   

         lat        lon  alone  not_alone  UTYP2  weekend  
0  52.583472  13.403228      0          1      7        0  
1  52.535255  13.432186      0          1      2        0  
2  52.514173  13.470897      0          1      2        0  
3  52.510848  13.394673      0          1      7        0  
4  52.458993  13.506372      0          1      2        0  

[5 rows x 21 columns]

In [4]:
df=df.drop(['Unnamed: 0'], axis=1)

In [5]:
df.head()

OBJECTID  UMONAT  USTUNDE  UWOCHENTAG  UKATEGORIE  UART  UTYP1  ULICHTVERH  \
0    112747       1       15           4           3     6      7           1   
1    112892       1       11           5           3     5      2           0   
2    112902       1        8           2           3     5      2           0   
3    112921       1       19           4           3     5      7           2   
4    112947       1       18           4           2     5      3           2   

   STRZUSTAND  IstPKW  IstKrad  IstGkfz  IstFuss  IstSonstige        lat  \
0           1       0        0        0        1            0  52.583472   
1           1       1        0        0        0            0  52.535255   
2           0       1        0        0        0            0  52.514173   
3           1       1        0        0        0            0  52.510848   
4           1       1        0        0        0            0  52.458993   

         lon  alone  not_alone  UTYP2  weekend  
0  13.403228      0          1      7        0  
1  13.432186      0          1      2        0  
2  13.470897      0          1      2        0  
3  13.394673      0          1      7        0  
4  13.506372      0          1      2        0

In [6]:
df.isna().sum()

OBJECTID       0
UMONAT         0
USTUNDE        0
UWOCHENTAG     0
UKATEGORIE     0
UART           0
UTYP1          0
ULICHTVERH     0
STRZUSTAND     0
IstPKW         0
IstKrad        0
IstGkfz        0
IstFuss        0
IstSonstige    0
lat            0
lon            0
alone          0
not_alone      0
UTYP2          0
weekend        0
dtype: int64

In [7]:
df.dtypes

OBJECTID         int64
UMONAT           int64
USTUNDE          int64
UWOCHENTAG       int64
UKATEGORIE       int64
UART             int64
UTYP1            int64
ULICHTVERH       int64
STRZUSTAND       int64
IstPKW           int64
IstKrad          int64
IstGkfz          int64
IstFuss          int64
IstSonstige      int64
lat            float64
lon            float64
alone            int64
not_alone        int64
UTYP2            int64
weekend          int64
dtype: object

In [8]:
#Berlin coordinates for folium
Berlin=[52.5200,13.4005]

In [9]:
#for the heatmap
df['constant']=1

In [10]:
map_berlin = folium.Map(location=Berlin,
                       zoom_start=12,
                       tiles='CartoDB dark_matter')
#other tiles: Stamen Toner #cartodbpositron
map_berlin

In [11]:
df.shape

(5192, 21)

In [12]:
[df['lat']][0][4]

52.458992961679954

In [13]:
map_points = folium.Map(location=Berlin,
                       zoom_start=12,
                       tiles='CartoDB dark_matter')
for i in range(0,5192): 
    folium.CircleMarker(location=[[df['lat']][0][i], [df['lon']][0][i]],
                       radius=2, stroke=False, fill_color='blue',
                        fill_opacity=0.5).add_to(map_points)
map_points

In [14]:
map_cluster = folium.Map(location=Berlin,
                       zoom_start=12,
                       tiles='CartoDB dark_matter')
cluster = folium.plugins.MarkerCluster().add_to(map_cluster)

for i in range(0,5192): 
    folium.Marker(location=[[df['lat']][0][i], [df['lon']][0][i]]).add_to(cluster)
map_cluster

In [15]:
heatmap = folium.Map(location=Berlin,
                       zoom_start=12,
                       tiles='CartoDB dark_matter')
HeatMap(data=df[['lat', 'lon', 'constant']].groupby(['lat', 'lon']).sum().reset_index().values.tolist(),
        radius=5, max_zoom=12).add_to(heatmap)
heatmap

In [16]:
heatmapwithtime = folium.Map(location=Berlin,
                       zoom_start=12,
                       tiles='Carto DB dark_matter')

hour_list=[[] for x in range(24)]

for lat,lon,hour in (zip(df.lat, df.lon, df.USTUNDE)):
    hour_list[hour].append([lat,lon])
    
index = [str(i)+':00' for i in range(24)]

HeatMapWithTime(hour_list, index, position='topright', auto_play=True).add_to(heatmapwithtime)
heatmapwithtime
#heatmapwithtime.save('heatmapwithtime.html')